In [65]:
import pandas as pd 
import requests 
import datetime as dt
import re
import json
from tqdm import tqdm
import os

from openai import OpenAI

#### SciencesPoC extract

In [26]:
df = pd.read_csv('/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/extract_sciences_po.csv')

In [28]:
df

Unnamed: 0                     item_id       date_published  \
0             0  I4OEKQ6MHRBP3LQVVYDDXW6T6U  2024-10-07 15:33:34   
1             1  LVA4MZBQOBECNPZD323NV6O7K4  2024-10-09 14:53:55   
2             2  4FAEHUUZ5ZFAJKLFEV2LT5CBAQ  2024-10-10 15:49:02   
3             3  4S4G6BKFRNER3LB22CLPAEWWKY  2024-10-11 15:28:25   
4             4  ZAFHRNAHJVC6THXRSBMCB4A24I  2024-10-09 10:55:05   
..          ...                         ...                  ...   
511         516  AOT254SA2VDIDNF4YW7XPLWJ5E  2024-10-12 15:46:00   
512         517  GUOUKHLPFZBK7GVR5XU7MXVD5A  2024-10-12 16:32:37   
513         518  5HT6C24ZBVDOBFXPLA4HNVOTT4  2024-10-12 16:33:57   
514         519  VLV6RSQ6U5E6XJ6AIRV26AEKO4  2024-10-12 16:43:33   
515         520  FVCJ6DQ5HVDNDGC4F6F276NVFM  2024-10-12 16:53:20   

                                                   url  \
0    https://www.liberation.fr/societe/familles/a-m...   
1    https://www.liberation.fr/sports/jeux-olympiqu...   
2    https://www.liberation.fr/international/afriqu...   
3    https://www.liberation.fr/economie/social/ferm...   
4    https://www.liberation.fr/lifestyle/design/pre...   
..                                                 ...   
511  https://www.liberation.fr/culture/musique/char...   
512  https://www.liberation.fr/societe/droits-des-f...   
513  https://www.liberation.fr/environnement/agricu...   
514  https://www.liberation.fr/economie/annonces-de...   
515  https://www.liberation.fr/economie/medias/budg...   

                                                 titre  \
0    Centre de loisirs à Marseille : sept plaintes ...   
1    JO de Paris 2024 : pour la santé mentale des a...   
2    Au Burkina Faso, la conscription pour «punir d...   
3    Fermeture de l’usine automobile MA France : «O...   
4    Près de Rouen, jardiner dans «un jeu subtil av...   
..                                                 ...   
511  Charlie Dalin : «Mon oncle était le chanteur d...   
512  Violences sexuelles : à la recherche de «co-vi...   
513  «Plus ils habitent près des champs, plus les t...   
514  Annonces de la Chine contre la crise économiqu...   
515  Budget 2025 : les radios associatives dénoncen...   

                                           description     type  \
0    Une enquête pour violences sur mineurs et diff...  article   
1    Avec la libération de la parole sur la santé m...  article   
2    Au moins sept magistrats ont été réquisitionné...  article   
3    Le 13 mai, l’entreprise sous-traitante de Stel...  article   
4    Imaginé par Patrick et Sylvie Quibel il y a tr...  article   
..                                                 ...      ...   
511  Charlie Dalin, skipper qui s’apprête à embarqu...  article   
512  Avec un système de «matchs», le site Coabuse r...  article   
513  Des traces de pesticides, dont certains interd...  article   
514  Face aux problèmes structurels de l’économie, ...  article   
515  Les radios associatives se sont alarmées vendr...  article   

                                                author  \
0                                    Caroline Delabroy   
1                                     Marie Thimonnier   
2                                         Agnès Faivre   
3                                          Eléna Roney   
4    ['Florian Bardou, envoyé spécial à Rouen', 'ph...   
..                                                 ...   
511                                     Alexis Bernier   
512                                     Hélène Coutard   
513                            [' LIBERATION', ' AFP']   
514                                    Arnaud Vaulerin   
515                            [' LIBERATION', ' AFP']   

                              section            subhead  premium  \
0                            Familles            Justice     True   
1    Jeux olympiques et paralympiques           Ecriture     True   
2                             Afrique         Répression    False   
3               

#### Connection API OpenAI

In [11]:
openaiClient = OpenAI()

In [ ]:
with open('/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/extract_sciences_po/2ALP47INTZG2PK4OF23FCSX47Q_gisèle_sapiro:«il_faut_être_traduit_pour_obtenir_le_nobel_et_en_même_temps_le_nobel_contribue_à_faire_traduire»_–_libération.txt', 'r') as f : 
    text = f.read()

with open('/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/prompt-favarel-et-al.txt', 'r') as f:
    prompt = f.read()

response = openaiClient.responses.create(
    model="gpt-4o",
    input=[
        {"role": "system", "content": prompt},
        {"role": "user", "content": text}
    ],
    text={
        "format": {
            "type": "json_schema",
            "name": "classification",
            "schema": {
                "type": "object",
                "properties": {
                    "categorie_princicpale": {
                        "type": "string"
                    },
                    "categorie_secondaire": {
                        "type": "string"
                    },
                },
                "required": ["categorie_princicpale", "categorie_secondaire"],
                "additionalProperties": False
            },
            "strict": True
        }
    }
)

#### Connect to Deepseek endpoint

In [ ]:
save_path = '/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/save'
content_path = '/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/extract_sciences_po'


def retrieve_classifications(name, mapping_prompt):


    if os.path.exists(f"{save_path}/output_{name}.txt"):
        with open(f"{save_path}/output_{name}.txt", 'r') as f : 
            out_dict = json.loads(f.read())
        out_df = pd.DataFrame.from_dict(out_dict)
        out = out_dict
    else : 
        out_df = pd.DataFrame(columns = ['item_id', 'categorie_principale', 'categorie_secondaire'])
        out = []

    df_to_process = df.loc[~df.item_id.isin(out_df.item_id)]

    if mapping_prompt[name]['client']=='deepseek':
        client = OpenAI(api_key=os.environ["DEEPSEEK_API_KEY"], base_url="https://api.deepseek.com")
    else:
        client=OpenAI()

    df_to_process = df.loc[~df.item_id.isin(out_df.item_id)]


    with open(mapping_prompt[name]['path_prompt'], 'r') as f:
        prompt = f.read()

    with tqdm(total=df_to_process.shape[0]) as pbar:
        for i, row in df_to_process.iterrows():
            titre_brut = f"{row.item_id}_"+row.titre.lower().strip().replace(f"\xa0", ' ').replace(' : ', ':').replace(' ', '_').replace('/', '')
            
            with open(f'{content_path}/{titre_brut}.txt', 'r') as f:
                text = f.read()

            messages = [{"role": "system", "content": prompt},
                        {"role": "user", "content": text}]

            response = client.chat.completions.create(
                model="deepseek-chat",
                messages=messages,
                response_format={
                    'type': 'json_object'
                }
            )
            try : 
                cat_json = json.loads(response.choices[0].message.content)

                out.append({
                    'item_id':row.item_id, 
                    'categorie_principale': cat_json['categorie_principale'],
                    'categorie_secondaire': cat_json['categorie_secondaire'],
                })
                
                with open(f'{save_path}/output_{name}.txt', 'w+') as f : 
                    f.write(json.dumps(out))

            except Exception as e : 
                print(f'Error with article {row.item_id}')
                pass

            
            pbar.update(1)



In [ ]:
with open('/Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/mapping_prompts.txt', 'r') as f : 
    mapping = json.loads(f.read())
retrieve_classifications('sans_titre_1', mapping)

  0%|          | 0/516 [00:00<?, ?it/s]

[04/03/25 18:33:21] INFO     HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 ]8;id=349282;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=148975;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py#1025\1025]8;;\
                             200 OK"                                                                               

  0%|          | 1/516 [00:07<1:03:24,  7.39s/it]

[04/03/25 18:33:28] INFO     HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 ]8;id=312204;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=977922;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py#1025\1025]8;;\
                             200 OK"                                                                               

  0%|          | 2/516 [00:14<1:01:39,  7.20s/it]

...

[04/03/25 18:37:02] INFO     HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 ]8;id=279816;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=646969;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py#1025\1025]8;;\
                             200 OK"                                                                               

  7%|▋         | 34/516 [03:47<53:44,  6.69s/it]

[04/03/25 18:37:08] INFO     HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 ]8;id=620591;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=720996;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py#1025\1025]8;;\
                             200 OK"                                                                               

  7%|▋         | 35/516 [03:54<52:17,  6.52s/it]

[04/03/25 18:37:15] INFO     HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 ]8;id=404706;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=821745;file:///Users/zsapey/Documents/Code/libe-datalab/Sciences-POC/.venv/lib/python3.11/site-packages/httpx/_client.py#1025\1025]8;;\
                             200 OK"                                                                               

#### Ajouter images